In [1]:
from datasets import load_dataset

minds = load_dataset("PolyAI/minds14", name="en-AU", split="train")

/Users/enricd/Code/Learning/hf_audio_course/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
from transformers import pipeline

classifier = pipeline(
    "audio-classification",
    model="anton-l/xtreme_s_xlsr_300m_minds14",
)

Device set to use mps:0


In [3]:
classifier(minds[0]["audio"])

[{'score': 0.9611988067626953, 'label': 'pay_bill'},
 {'score': 0.029601838439702988, 'label': 'freeze'},
 {'score': 0.003550308756530285, 'label': 'card_issues'},
 {'score': 0.0021323123946785927, 'label': 'abroad'},
 {'score': 0.0008829645812511444, 'label': 'high_value_payment'},
 {'score': 0.0007431716658174992, 'label': 'direct_debit'},
 {'score': 0.0004143833357375115, 'label': 'latest_transactions'},
 {'score': 0.00034886455978266895, 'label': 'joint_account'},
 {'score': 0.0003365074226167053, 'label': 'address'},
 {'score': 0.00032862869556993246, 'label': 'balance'},
 {'score': 0.00015601288760080934, 'label': 'app_error'},
 {'score': 0.0001500186772318557, 'label': 'atm_limit'},
 {'score': 8.987434557639062e-05, 'label': 'cash_deposit'},
 {'score': 6.637127080466598e-05, 'label': 'business_loan'}]

In [4]:
speech_commands = load_dataset(
    "speech_commands", 
    "v0.02", 
    split="validation", 
    streaming=True, 
    trust_remote_code=True
)
sample = next(iter(speech_commands))

In [5]:
sample

{'file': 'backward/0d82fd99_nohash_2.wav',
 'audio': {'path': 'backward/0d82fd99_nohash_2.wav',
  'array': array([-9.15527344e-05,  6.10351562e-05,  6.10351562e-05, ...,
          2.68859863e-02,  1.46179199e-02,  1.67846680e-03], shape=(16000,)),
  'sampling_rate': 16000},
 'label': 30,
 'is_unknown': True,
 'speaker_id': '0d82fd99',
 'utterance_id': 2}

In [6]:
classifier = pipeline(
    "audio-classification", 
    model="MIT/ast-finetuned-speech-commands-v2"
)
classifier(sample["audio"].copy())[:5]

Device set to use mps:0


[{'score': 0.9999891519546509, 'label': 'backward'},
 {'score': 1.7504869447293459e-06, 'label': 'happy'},
 {'score': 6.703020289933193e-07, 'label': 'follow'},
 {'score': 5.805883915854793e-07, 'label': 'stop'},
 {'score': 5.614541009890672e-07, 'label': 'up'}]

In [7]:
from IPython.display import Audio

Audio(sample["audio"]["array"], rate=sample["audio"]["sampling_rate"])

In [ ]:
# Language Identification with FLEURS

fleurs = load_dataset("google/fleurs", "all", split="validation", streaming=True)
sample = next(iter(fleurs))

In [ ]:
classifier = pipeline(
    "audio-classification", model="sanchit-gandhi/whisper-medium-fleurs-lang-id"
)

In [ ]:
classifier(sample["audio"])

In [ ]:
# Zero-Shot Audio Classification

dataset = load_dataset(
    "ashraq/esc50", 
    split="train", 
    streaming=True
)
audio_sample = next(iter(dataset))["audio"]["array"]

In [ ]:
candidate_labels = ["Sound of a dog", "Sound of vacuum cleaner"]

In [ ]:
classifier = pipeline(
    task="zero-shot-audio-classification", 
    model="laion/clap-htsat-unfused"
)
classifier(audio_sample, candidate_labels=candidate_labels)

In [ ]:
Audio(audio_sample, rate=16000)


### 03 Fine-tuning a model for Music Classification

In [1]:
# Dataset for music genre classification

from datasets import load_dataset

gtzan = load_dataset(
    "marsyas/gtzan", 
    "all",
    trust_remote_code=True)
gtzan

DatasetDict({
    train: Dataset({
        features: ['file', 'audio', 'genre'],
        num_rows: 999
    })
})

In [2]:
gtzan = gtzan["train"].train_test_split(seed=42, shuffle=True, test_size=0.1)
gtzan

DatasetDict({
    train: Dataset({
        features: ['file', 'audio', 'genre'],
        num_rows: 899
    })
    test: Dataset({
        features: ['file', 'audio', 'genre'],
        num_rows: 100
    })
})

In [3]:
gtzan["train"][0]

{'file': '/Users/enricd/.cache/huggingface/datasets/downloads/extracted/40c07343237752829edcbe5f423b0da1fd2d1dba7d675bc80b8c246373d750e8/genres/pop/pop.00098.wav',
 'audio': {'path': '/Users/enricd/.cache/huggingface/datasets/downloads/extracted/40c07343237752829edcbe5f423b0da1fd2d1dba7d675bc80b8c246373d750e8/genres/pop/pop.00098.wav',
  'array': array([ 0.10720825,  0.16122437,  0.28585815, ..., -0.22924805,
         -0.20629883, -0.11334229], shape=(661504,)),
  'sampling_rate': 22050},
 'genre': 7}

In [4]:
gtzan["train"].features

{'file': Value(dtype='string', id=None),
 'audio': Audio(sampling_rate=22050, mono=True, decode=True, id=None),
 'genre': ClassLabel(names=['blues', 'classical', 'country', 'disco', 'hiphop', 'jazz', 'metal', 'pop', 'reggae', 'rock'], id=None)}

In [5]:
id2label_fn = gtzan["train"].features["genre"].int2str
id2label_fn(gtzan["train"][0]["genre"])

'pop'

In [6]:
from IPython.display import Audio

def generate_audio():
    example = gtzan["train"].shuffle()[0]
    audio = example["audio"]
    return (
        audio["sampling_rate"],
        audio["array"]
    ), id2label_fn(example["genre"])

for _ in range(4):
    audio, label = generate_audio()
    print(f"Label: {label}")
    display(Audio(audio[1], rate=audio[0]))

Label: pop


Label: classical


Label: disco


Label: pop


In [7]:
from transformers import AutoFeatureExtractor

model_id = "ntu-spml/distilhubert"
feature_extractor = AutoFeatureExtractor.from_pretrained(
    model_id, do_normalize=True, return_attention_mask=True
)

In [8]:
sampling_rate = feature_extractor.sampling_rate
sampling_rate

16000

In [9]:
from datasets import Audio

gtzan = gtzan.cast_column("audio", Audio(sampling_rate=sampling_rate))

gtzan["train"][0]

{'file': '/Users/enricd/.cache/huggingface/datasets/downloads/extracted/40c07343237752829edcbe5f423b0da1fd2d1dba7d675bc80b8c246373d750e8/genres/pop/pop.00098.wav',
 'audio': {'path': '/Users/enricd/.cache/huggingface/datasets/downloads/extracted/40c07343237752829edcbe5f423b0da1fd2d1dba7d675bc80b8c246373d750e8/genres/pop/pop.00098.wav',
  'array': array([ 0.08735093,  0.20183384,  0.47908676, ..., -0.1874318 ,
         -0.23294398, -0.13517429], shape=(480003,)),
  'sampling_rate': 16000},
 'genre': 7}

In [10]:
import numpy as np

sample = gtzan["train"][0]["audio"]

print(f"Mean: {np.mean(sample['array']):.3}, Variance: {np.var(sample['array']):.3}")

Mean: 0.000185, Variance: 0.0493


In [11]:
inputs = feature_extractor(sample["array"], sampling_rate=sample["sampling_rate"])

print(f"inputs keys: {list(inputs.keys())}")

print(
    f"Mean: {np.mean(inputs['input_values']):.3}, Variance: {np.var(inputs['input_values']):.3}"
)

inputs keys: ['input_values', 'attention_mask']
Mean: -7.01e-09, Variance: 1.0


In [12]:
max_duration = 30.0


def preprocess_function(examples):
    audio_arrays = [x["array"] for x in examples["audio"]]
    inputs = feature_extractor(
        audio_arrays,
        sampling_rate=feature_extractor.sampling_rate,
        max_length=int(feature_extractor.sampling_rate * max_duration),
        truncation=True,
        return_attention_mask=True,
    )
    return inputs

In [13]:
gtzan_encoded = gtzan.map(
    preprocess_function,
    remove_columns=["audio", "file"],
    batched=True,
    batch_size=100,
    num_proc=1,
)
gtzan_encoded

DatasetDict({
    train: Dataset({
        features: ['genre', 'input_values', 'attention_mask'],
        num_rows: 899
    })
    test: Dataset({
        features: ['genre', 'input_values', 'attention_mask'],
        num_rows: 100
    })
})

In [14]:
gtzan_encoded = gtzan_encoded.rename_column("genre", "label")

In [15]:
id2label = {
    str(i): id2label_fn(i)
    for i in range(len(gtzan_encoded["train"].features["label"].names))
}
label2id = {v: k for k, v in id2label.items()}

id2label["7"]

'pop'

In [16]:
# Fine-tuning the model

from transformers import AutoModelForAudioClassification

num_labels = len(id2label)

model = AutoModelForAudioClassification.from_pretrained(
    model_id,
    num_labels=num_labels,
    label2id=label2id,
    id2label=id2label,
)

Some weights of HubertForSequenceClassification were not initialized from the model checkpoint at ntu-spml/distilhubert and are newly initialized: ['classifier.bias', 'classifier.weight', 'projector.bias', 'projector.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [17]:
# Hugging Face Hub
# from huggingface_hub import notebook_login

# notebook_login()

In [18]:
from transformers import TrainingArguments

model_name = model_id.split("/")[-1]
batch_size = 8
gradient_accumulation_steps = 1
num_train_epochs = 10

training_args = TrainingArguments(
    f"{model_name}-finetuned-gtzan",
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=5e-5,
    per_device_train_batch_size=batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=num_train_epochs,
    warmup_ratio=0.1,
    logging_steps=5,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    fp16=False,
    # push_to_hub=True,
)

In [19]:
import evaluate
import numpy as np

metric = evaluate.load("accuracy")


def compute_metrics(eval_pred):
    """Computes accuracy on a batch of predictions"""
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return metric.compute(predictions=predictions, references=eval_pred.label_ids)

In [20]:
from transformers import Trainer

trainer = Trainer(
    model,
    training_args,
    train_dataset=gtzan_encoded["train"],
    eval_dataset=gtzan_encoded["test"],
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)

trainer.train()

/var/folders/4w/wv1fjnjn2l5b6kzwv57x8ltw0000gn/T/ipykernel_7548/2059408770.py:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
/Users/enricd/Code/Learning/hf_audio_course/.venv/lib/python3.13/site-packages/torch/utils/data/dataloader.py:684: UserWarning: 'pin_memory' argument is set as true but not supported on MPS now, then device pinned memory won't be used.
  warnings.warn(warn_msg)


KeyboardInterrupt: 

In [ ]:
# Push ckpt and metrics score to Leaderboard

kwargs = {
    "dataset_tags": "marsyas/gtzan",
    "dataset": "GTZAN",
    "model_name": f"{model_name}-finetuned-gtzan",
    "finetuned_from": model_id,
    "tasks": "audio-classification",
}

trainer.push_to_hub(**kwargs)

In [ ]:
# Share Model

from transformers import pipeline

pipe = pipeline(
    "audio-classification", model="sanchit-gandhi/distilhubert-finetuned-gtzan"
)